# Homework 2 (Due 11:59pm PST March 31st, 2020): Word Vectorization, Regex Practice, and Similarity

A. Using the **McDonalds Yelp Review CSV file**, **process the reviews**.
This means:
* what stopwords to remove
* what regex cleaning you may need to perform (for example, are there different ways of saying `hamburger` that you need to account for?)
* stemming/lemmatization

however you deem appropriate using the tools we have learned today (tokenizing, stemming, lemmatization, removing stopwords), and **produce a correlation matrix** of the top 300 words by frequency. Then, **sample your dataframe for only the top 200 words, and identify the two reviews that are the most "similar" based upon cosine similarity**.

In [1]:
import codecs
file = "mcdonalds-yelp-negative-reviews.csv"
text = codecs.open(file,"r","latin1").readlines()

In [2]:
text = list(map(lambda review: review.replace('\n', '').replace('\\\\', '').replace('/',' '), text))

In [3]:
#text

In [4]:
import re
cleaned_text=[]
for t in text:
    #cleaned_text.append(re.sub(r'(?:)[0-9][aApP][mM]\b', 'TIMEVALUE', t))
    t1=re.sub(r'([0-9]|0[0-9]|1[0-9]|2[0-3]):([0-5][0-9])\s*([AaPp][Mm])','TIMEVALUE',t)
    t2=re.sub(r'[0-9]{1,2}\s*([AaPp][Mm])','TIMEVALUE',t1)
    t3=re.sub(r'[0-9]{9}','',t2)
    tt=re.sub(r'\\\\','',t3)
    cleaned_text.append(tt)

In [5]:
#cleaned_text

In [6]:
from nltk.corpus import stopwords
#print(set(stopwords.words('english')))

In [7]:
sw = set(stopwords.words('english'))
sw.add('mcdonald')
sw.add('mcdonald\'s')
sw.add('mcdonalds')
sw.add('mcd')
sw.add('order')
sw.add('really')
sw.add('thing')
sw.add('usually')
sw.add('actually')
sw.add('oh')
sw.add('probably')
sw.add('come')

In [8]:
cleaned_reviews = []

for review in cleaned_text:
    words = review[1:].split()
    new_words = []
    for word in words:
        if word.lower() in sw:
            continue
        new_words.append(word)
    cleaned_review = " ".join(new_words)
    cleaned_reviews.append((cleaned_review))

In [9]:
cleaned_reviews.remove('unit_id,city,review')

In [10]:
#cleaned_reviews

In [11]:
from nltk.stem import WordNetLemmatizer
from nltk import word_tokenize
import string
lemmatizer = WordNetLemmatizer()
result = []
for t in cleaned_reviews:
    words = word_tokenize(t)
    final = []
    for w in words:
        final.append(lemmatizer.lemmatize(w).strip(string.punctuation))
    res = " ".join(final)
    result.append(res)

In [12]:
#result

In [13]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer

vectorizer = CountVectorizer(stop_words="english")
vector = vectorizer.fit_transform(result)

# convert into Pandas dataframe
count_df = pd.DataFrame(vector.toarray(), columns=vectorizer.get_feature_names())

In [14]:
#count_df

# Correlation matrix for top 300 words

In [15]:
top_300_words = count_df.sum(axis=0).sort_values(ascending=False)[:300].index.values

In [16]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

top_300_count_df = count_df[top_300_words]
top_300_count_df.corr()

food      time     drive   service     place      like  \
food          1.000000  0.236916  0.085229  0.225600  0.136694  0.121803   
time          0.236916  1.000000  0.142726  0.120338  0.158998  0.063811   
drive         0.085229  0.142726  1.000000  0.120054  0.014890  0.050188   
service       0.225600  0.120338  0.120054  1.000000  0.094975  0.035374   
place         0.136694  0.158998  0.014890  0.094975  1.000000  0.162302   
like          0.121803  0.063811  0.050188  0.035374  0.162302  1.000000   
vegas         0.009564 -0.019135  0.040354  0.019132 -0.038479 -0.007119   
las           0.005132 -0.022410  0.036369  0.015525 -0.035956 -0.005867   
location      0.120545  0.155609  0.126266  0.108197  0.099173  0.077077   
people        0.151315  0.130094  0.046096  0.071598  0.185135  0.166704   
order         0.165795  0.239880  0.187927  0.147504  0.101790  0.032496   
fry           0.123307  0.122706  0.054908 -0.008495  0.018618  0.143643   
got           0.127606  0.151903  0.126561  0.038762  0.062592  0.099779   
ve            0.106135  0.249886  0.098107  0.130328  0.095313  0.094991   
customer      0.160622  0.125552  0.054150  0.371766  0.073683  0.079637   
new           0.033876  0.019929 -0.088384 -0.037686  0.059738  0.088606   
good          0.107248 -0.003136  0.032255  0.080751  0.073257  0.067192   
minute        0.155917  0.171598  0.137213  0.107377  0.057227  0.075769   
coffee       -0.032372  0.047934  0.012802 -0.001156 -0.004457  0.051380   
window        0.092699  0.067633  0.346235  0.068952  0.001197  0.055227   
ordered       0.178020  0.133041  0.161200  0.098492  0.042431  0.126452   
line          0.131758  0.117387  0.103613  0.058205  0.114139  0.053089   
right         0.152869  0.196365  0.116492  0.141155  0.111789  0.117165   
went          0.140775  0.163546  0.166587  0.037859  0.047063  0.102906   
manager       0.055857  0.093268 -0.012907  0.134985  0.007302  0.083017   
mcdonald      0.130133  0.038149  0.047913  0.001424  0.020888  0.149831   
fast          0.465092  0.106228  0.081691  0.084422  0.064833  0.042330   
chicago      -0.002556  0.029633 -0.075795  0.015731  0.096832 -0.009905   
know          0.167734  0.163444  0.124103  0.121526  0.121591  0.170142   
worst         0.099400  0.110158  0.093620  0.175304 -0.023596  0.038707   
say           0.083373  0.111639  0.132569  0.102307  0.084181  0.156653   
staff         0.052539  0.079526 -0.006593  0.039000  0.139651  0.053240   
work          0.116124  0.179937  0.094698  0.120487  0.131587  0.090588   
make          0.132586  0.175884  0.100239  0.079779  0.139586  0.098582   
way           0.103010  0.088993  0.151408  0.044688  0.073433  0.072391   
employee      0.164340  0.083101  0.093848  0.184459  0.030149  0.029435   
said          0.072288  0.026233  0.133403  0.089383  0.055991  0.117258   
mcdonalds     0.051917  0.092283  0.012724  0.040772  0.074604  0.060683   
want          0.091404  0.075959  0.051775  0.073442  0.145338  0.154854   
breakfast     0.031144  0.065982  0.066491  0.071217  0.032643  0.016799   
bad           0.095924  0.095563  0.076893  0.141347  0.030654  0.093948   
wait          0.145210  0.150356  0.137571  0.066712  0.087624  0.022591   
wrong         0.074553  0.215128  0.099160  0.101933  0.038528  0.056220   
meal          0.112291  0.115138  0.028221  0.023970  0.051518  0.101722   
inside        0.044724  0.097147  0.161989  0.041349  0.143258  0.075660   
asked         0.125212  0.013706  0.106757  0.073225  0.021397  0.081959   
york         -0.020930 -0.007904 -0.177716 -0.049479  0.021650  0.042772   
burger        0.085600  0.158459  0.038808  0.011672  0.034170  0.088187   
car           0.152358  0.094569  0.349754  0.061179  0.081305  0.067627   
need          0.053574  0.065635  0.047355  0.002907  0.121281  0.074744   
eat           0.194190  0.076402  0.019623  0.040505  0.192423  0.128894   
angeles       0.007328  0.021447  0.057407 -0.041817  0.031352  0.

# Top 200 word dataframe

In [17]:
top_200 = top_300_count_df[:200]
top_200.head()

food  time  drive  service  place  like  vegas  las  location  people  \
0     0     1      1        0      0     0      0    0         0       0   
1     2     0      0        1      0     0      0    0         0       0   
2     0     0      0        0      0     0      0    0         0       0   
3     0     0      0        0      0     0      0    0         0       0   
4     1     2      0        2      1     0      0    0         2       0   

   order  fry  got  ve  customer  new  good  minute  coffee  window  ordered  \
0      0    0    0   2         0    0     0       0       0       0        0   
1      0    0    0   0         1    0     0       1       0       1        0   
2      3    0    0   0         0    0     0       2       0       0        0   
3      0    0    0   0         0    0     0       0       0       0        0   
4      0    0    0   0         0    0     0       1       0       0        0   

   line  right  went  manager  mcdonald  fast  chicago  know  worst  say  \
0     0      0     0        0         0     0        0     0      1    0   
1     0      0     1        0         0     0        0     0      0    1   
2     0      0     0        1         0     0        0     0      0    0   
3     0      0     0        0         0     0        0     0      0    1   
4     0      0     0        0         1     0        0     2      0    0   

   staff  work  make  way  employee  said  mcdonalds  want  breakfast  bad  \
0      1     0     0    0         0     0          0     0          0    0   
1      0     0     0    1         0     0          0     0          0    0   
2      0     0     0    0         0     2          0     0          1    0   
3      0     0     0    0         0     0          0     0          0    0   
4      0     0     0    0         0     0          0     0          0    0   

   wait  wrong  meal  inside  asked  york  burger  car  need  eat  angeles  \
0     0      0     0       1      0     0       0    0     0    0        0   
1     0      0     0       2      0     0       0    0     0    0        0   
2     0      0     0       0      3     0       0    0     0    0        0   
3     0      0     0       0      0     0       0    0     1    0        0   
4     1      0     0       0      0     0       0    0     0    1        0   

   los  star  long  day  going  restaurant  waiting  review  took  think  \
0    0     0     0    0      0           0        0       0     0      0   
1    0     0     0    0      0           0        1       0     0      0   
2    0     0     0    0      0           0        1       0     1      0   
3    0     2     0    0      0           0        0       0     0      0   
4    0     0     0    0      0           0        0       2     0      0   

   chicken  pretty  night  big  told  slow  drink  timevalue  ask  hour  \
0        0       0      0    0     0     0      0          0    0     0   
1        0       0      0    0     0     0      0          1    0     0   
2        0       0      0    0     0     0      0          0    1     0   
3        0       0      0    0     0     0      0          0    0     0   
4        0       0      0    0     0     0      0          0    1     0   

   sandwich  atlanta  area  morning  nice  hot  better  sauce  10  kid  came  \
0         0        1     0        0     0    0       1      0   0    0     0   
1         0        1     0        0     0    0       0      0   0    0     1   
2         0        1     0        0     0    0       0      0   0    0     0   
3         0        1     0        0     0    0       0      0   0    0     0   
4         0        1     1        0     0    0       1      0   0    0     0   

   guy  rude  cashier  lot  sure  look  ca  cold  experience  quick  menu  \
0    0     0        0    0     0     0   0     0           0      0     0   
1    0     0        0    0     0     0   0     0           0      0     0   
2    0     0        0    0     0     0   0     0  

In [18]:
# top 200 words
top_200.columns

Index(['food', 'time', 'drive', 'service', 'place', 'like', 'vegas', 'las',
       'location', 'people',
       ...
       'bite', 'quite', 'mickey', '30', 'world', 'giving', 'craving', 'charge',
       'cone', 'english'],
      dtype='object', length=300)

# Cosine similarity

In [19]:
from sklearn.metrics.pairwise import cosine_similarity

vector = vectorizer.fit_transform(result)
similarity_matrix = cosine_similarity(vector)
similarity_matrix

array([[1.        , 0.10619885, 0.04733811, ..., 0.04199605, 0.04243489,
        0.02916059],
       [0.10619885, 1.        , 0.14076307, ..., 0.21853669, 0.04206101,
        0.02167775],
       [0.04733811, 0.14076307, 1.        , ..., 0.02087414, 0.0492153 ,
        0.10145993],
       ...,
       [0.04199605, 0.21853669, 0.02087414, ..., 1.        , 0.03742406,
        0.07715167],
       [0.04243489, 0.04206101, 0.0492153 , ..., 0.03742406, 1.        ,
        0.11260583],
       [0.02916059, 0.02167775, 0.10145993, ..., 0.07715167, 0.11260583,
        1.        ]])

In [20]:
sim = pd.DataFrame(similarity_matrix)

In [21]:
sim.head()

0         1         2         3         4         5         6     \
0  1.000000  0.106199  0.047338  0.072739  0.100791  0.102869  0.031497   
1  0.106199  1.000000  0.140763  0.108148  0.112390  0.038236  0.140488   
2  0.047338  0.140763  1.000000  0.036155  0.050098  0.051131  0.015656   
3  0.072739  0.108148  0.036155  1.000000  0.038490  0.078567  0.096225   
4  0.100791  0.112390  0.050098  0.038490  1.000000  0.054433  0.183333   

       7         8         9         10        11        12        13    \
0  0.091003  0.160032  0.145479  0.107443  0.071750  0.190757  0.074848   
1  0.050738  0.163579  0.198271  0.179713  0.106676  0.078782  0.194745   
2  0.180933  0.198860  0.036155  0.026702  0.035663  0.115886  0.018602   
3  0.104257  0.030557  0.074074  0.041030  0.109599  0.097129  0.114332   
4  0.072232  0.148192  0.205280  0.156347  0.056949  0.168232  0.138621   

       14        15        16        17        18        19        20    \
0  0.060523  0.231455  0.062994  0.097590  0.202610  0.138013  0.091003   
1  0.179969  0.114708  0.234146  0.036274  0.060248  0.153897  0.067651   
2  0.030083  0.115045  0.031311  0.024254  0.030212  0.034300  0.022617   
3  0.092450  0.235702  0.096225  0.074536  0.061898  0.105409  0.139010   
4  0.192154  0.081650  0.133333  0.103280  0.117932  0.109545  0.048154   

       21        22        23        24        25        26        27    \
0  0.063888  0.033375  0.178174  0.215249  0.056344  0.133631  0.055427   
1  0.205805  0.086838  0.165567  0.026669  0.041885  0.099340  0.164817   
2  0.148192  0.182480  0.044281  0.017832  0.028006  0.066421  0.068875   
3  0.065060  0.076472  0.068041  0.054800  0.258199  0.136083  0.127000   
4  0.067612  0.052981  0.117851  0.132882  0.029814  0.094281  0.205306   

       28        29        30        31        32        33        34    \
0  0.058321  0.043644  0.078246  0.089087  0.121046  0.257894  0.050063   
1  0.130066  0.064889  0.174503  0.066227  0.022496  0.117979  0.055824   
2  0.057977  0.043386  0.220389  0.177123  0.015041  0.029581  0.124418   
3  0.089087  0.066667  0.039841  0.136083  0.046225  0.030303  0.038236   
4  0.092582  0.023094  0.082808  0.047140  0.144115  0.241437  0.132453   

       35        36        37        38        39        40        41    \
0  0.069007  0.082479  0.040522  0.097590  0.062000  0.045502  0.039841   
1  0.051299  0.061314  0.120495  0.036274  0.184362  0.033826  0.266557   
2  0.034300  0.040996  0.040283  0.024254  0.110062  0.135699  0.059409   
3  0.105409  0.125988  0.061898  0.074536  0.040589  0.139010  0.060858   
4  0.036515  0.087287  0.042885  0.077460  0.135917  0.120386  0.231900   

       42        43        44        45        46        47        48    \
0  0.047619  0.192879  0.146385  0.105851  0.069007  0.115142  0.178174   
1  0.141598  0.086031  0.036274  0.157378  0.051299  0.085595  0.154529   
2  0.071007  0.019174  0.097014  0.026307  0.034300  0.073583  0.059041   
3  0.145479  0.058926  0.074536  0.080845  0.105409  0.075378  0.136083   
4  0.075593  0.122474  0.025820  0.084017  0.109545  0.060927  0.235702   

       49        50        51        52        53        54        55    \
0  0.125988  0.089924  0.222718  0.092582  0.125988  0.181848  0.240981   
1  0.093659  0.044566  0.033113  0.045883  0.046829  0.189258  0.071657   
2  0.062622  0.059595  0.022140  0.092036  0.062622  0.018078  0.083846   
3  0.192450  0.091574  0.068041  0.094281  0.096225  0.055556  0.147242   
4  0.066667  0.047583  0.023570  0.016330  0.033333  0.038490  0.114764   

       56        57        58        59        60        61        62    \
0  0.125988  0.111943  0.162650  0.097590  0.091003  0.037702  0.130120   
1  0.046829  0.066574  0.096730  0.217643  0.101477  0.098097  0.096730   
2  0.031311  0.044513  0.113183  0.048507  0.022617  0.093700  0.129352   
3  0.096225  0.068399  0.049690  0.074536  0.069505  0.028796  0.049690   
4  0.066667  0.142164  0

In [22]:
s = sim[sim<0.9999999999]
s.max().idxmax()

139

In [23]:
s.iloc[139].idxmax()

140

In [24]:
s.iloc[139,140]==s.max().max()

True

# Two reviews that are most simiar

In [25]:
text[139:141]

['679455792,Las Vegas,"The worst service ever. And I\'m not a rude person, at all. I said ""please"" and ""thank you."" And I absolutely was not greeted whatsoever. Whoever that dumbass lady was, that was working needs to take that stick out of her. Don\'t be mad at me \'cause you hate YOUR job, bitch. Let\'s not forget that everyone is REPLACEABLE, including your miserable self. It took every bit of me not to cuss her out. I\'d write a letter to corporate but she did not give me a receipt. Go figure right. I\'m not one to talk down on people that works fast food because it\'s not in my character to knock someone\'s hustle. But she really needs to get it together. And for that, I will NOT ever return to this McDonald\'s ever again. Some bullshit. Oh. And. Not only did I not get a receipt... I didn\'t get a straw. And instead of 10 piece chicken nuggets, I got 9. What in the fucking fuck..... Fuck that McDonalds."',
 '679455793,Las Vegas,"Worst McDonalds EVER!!!!!!!!!! They are unable t

B. Complete all remaining exercises in **Regex Practice (Part II)**.

In [26]:
import codecs
file = "tale-of-two-cities.txt"
text = codecs.open(file,"r","latin1").readlines()

In [27]:
text = list(map(lambda review: review.replace('\n', ''), text))
t = " ".join(text)

In [28]:
import nltk
sent_text = nltk.sent_tokenize(t) # this gives us a list of sentences
#sent_text

# Stemming

In [29]:
from nltk import word_tokenize
import string
stemmer = nltk.stem.porter.PorterStemmer()
result = []
for sent in sent_text:
    words = word_tokenize(sent)
    final = []
    for w in words:
        final.append(stemmer.stem(w).strip(string.punctuation))
    res = " ".join(final)
    result.append(res)

In [30]:
#result

In [31]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer = CountVectorizer()
X = vectorizer.fit_transform(result) 
X = X.toarray()

In [32]:
import pandas as pd
corpus_df = pd.DataFrame(X, columns=vectorizer.get_feature_names())
corpus_df.head()

1757  1767  1792  21  aback  abandon  abash  abat  abbay  abbaye  abe  \
0     0     0     0   0      0        0      0     0      0       0    0   
1     0     0     0   0      0        0      0     0      0       0    0   
2     0     0     0   0      0        0      0     0      0       0    0   
3     0     0     0   0      0        0      0     0      0       0    0   
4     0     0     0   0      0        0      0     0      0       0    0   

   abhorr  abid  abil  abject  abl  ablaz  abneg  aboard  abod  abolish  \
0       0     0     0       0    0      0      0       0     0        0   
1       0     0     0       0    0      0      0       0     0        0   
2       0     0     0       0    0      0      0       0     0        0   
3       0     0     0       0    0      0      0       0     0        0   
4       0     0     0       0    0      0      0       0     0        0   

   abolished  abolit  abomin  abound  about  abov  abreast  abridg  abroad  \
0          0       0       0       0      0     0        0       0       0   
1          0       0       0       0      0     0        0       0       0   
2          0       0       0       0      0     0        0       0       0   
3          0       0       0       0      0     0        0       0       0   
4          0       0       0       0      0     0        0       0       0   

   abrupt  abruptli  absenc  absent  absolut  absolv  absorb  absorpt  \
0       0         0       0       0        0       0       0        0   
1       0         0       0       0        0       0       0        0   
2       0         0       0       0        0       0       0        0   
3       0         0       0       0        0       0       0        0   
4       0         0       0       0        0       0       0        0   

   abstract  abstractedli  absurd  abund  abus  abyss  abyssinia  accent  \
0         0             0       0      0     0      0          0       0   
1         0             0       0      0     0      0          0       0   
2         0             0       0      0     0      0          0       0   
3         0             0       0      0     0      0          0       0   
4         0             0       0      0     0      0          0       0   

   accept  access  accessori  accid  accident  acclam  accommod  accompani  \
0       0       0          0      0         0       0         0          0   
1       0       0          0      0         0       0         0          0   
2       0       0          0      0         0       0         0          0   
3       0       0          0      0         0       0         0          0   
4       0       0          0      0         0       0         0          0   

   accomplic  accomplish  accord  accordingli  accost  account  accoutr  \
0          0           0       0            0       0        0        0   
1          0           0       0            0       0        0        0   
2          0           0       0            0       0        0        0   
3          0           0       0            0       0        0        0   
4          0           0       0            0       0        0        0   

   accumul  accur  accurs  accus  accustom  ace  achiev  acknowledg  acoust  \
0        0      0       0      0         0    0       0           0       0   
1        0      0       0      0         0    0       0           0       0   
2        0      0       0      0         0    0       0           0       0   
3        0      0       0      0         0    0       0           0       0   
4        0      0       0      0         0    0       0           0       0   

   acquaint  acquiesc  acquir  acquirements  acquisit  acquit  acquitt  acr  \
0         0         0       0             0         0       0        0    0   
1         0         0       0             0         0       0        0    0   
2         0         0       0             0         0       0        0    0   
3         0        

In [33]:
corpus_df.shape

(7764, 6659)

# Lemmatizer

In [34]:
from nltk.stem import WordNetLemmatizer
import string
lemmatizer = WordNetLemmatizer()
result = []
for sent in sent_text:
    words = word_tokenize(sent)
    final = []
    for w in words:
        final.append(lemmatizer.lemmatize(w).strip(string.punctuation))
    res = " ".join(final)
    result.append(res)

In [35]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer = CountVectorizer()
X = vectorizer.fit_transform(result) 
X = X.toarray()

In [36]:
import pandas as pd
corpus_df = pd.DataFrame(X, columns=vectorizer.get_feature_names())
corpus_df.shape

(7764, 8910)

# Lemmatizer + Stopwords

In [37]:
from nltk.stem import WordNetLemmatizer
import string
lemmatizer = WordNetLemmatizer()
result = []
for sent in sent_text:
    words = word_tokenize(sent)
    final = []
    for w in words:
        final.append(lemmatizer.lemmatize(w).strip(string.punctuation))
    res = " ".join(final)
    result.append(res)

In [38]:
from nltk.corpus import stopwords
sw = set(stopwords.words('english'))
cleaned = []

for text in result:
    words = text.split()
    new_words = []
    for word in words:
        if word.lower() in sw:
            continue
        new_words.append(word)
    cleaned_text = " ".join(new_words)
    cleaned.append((cleaned_text))

In [39]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer = CountVectorizer()
X = vectorizer.fit_transform(cleaned) 
X = X.toarray()
corpus_df = pd.DataFrame(X, columns=vectorizer.get_feature_names())
corpus_df.shape

(7764, 8811)

For stemming, I get 6659 features; for lemmatizer only, I get 8910 features; for leammtizer combined with removing stopwords, I get 8811 words.